In [15]:
import numpy as np
import pandas as pd
import os

from transformers import AutoTokenizer, AutoModelForCausalLM, AutoConfig, BitsAndBytesConfig
import torch
from llava.model import LlavaLlamaForCausalLM
from llava.model.language_model.llava_llama import LlavaLlamaForCausalLM

os.environ["TRANSFORMERS_CACHE"] = "/Data2/Arun-UAV/NLP/hugginface_cache"
os.environ["HF_HOME"] = "/Data2/Arun-UAV/NLP/hugginface_cache"

/home/user/.conda/envs/vision_halu/lib/python3.10/site-packages/torch/cuda/__init__.py:61: FutureWarning: The pynvml package is deprecated. Please install nvidia-ml-py instead. If you did not install pynvml directly, please report this to the maintainers of the package that installed pynvml for you.
  import pynvml  # type: ignore[import]


In [16]:
# model_path = "liuhaotian/llava-v1.5-7b"
# kwargs = {'device_map': 'auto', 'torch_dtype': torch.float16}

# tokenizer = AutoTokenizer.from_pretrained(model_path, use_fast=False)
# model = LlavaLlamaForCausalLM.from_pretrained(
#     model_path,
#     low_cpu_mem_usage=True,
#     **kwargs
# )

In [17]:
from datasets import load_dataset

In [18]:
df = pd.read_json("/Data2/Arun-UAV/NLP/vision_halu/haloc/train_dataset/qa_database.json")

In [19]:
df.shape

(159612, 10)

In [21]:
df.head()

image_id question_id semantic_type detailed_type hallucination_type  \
0   2411114   001000046     attribute      position              other   
1   2411114   001000113     attribute      material              other   
2   2411114   001000255     attribute      position              other   
3   2411114   001000300  relationship        object              other   
4   2411114   001000301  relationship        object              other   

                                            question original_answer  \
0                       On which side is the helmet?            left   
1  Which material was used to make the planter, c...        concrete   
2            On which side of the photo is the lamp?           right   
3                              On what is that lamp?            post   
4                               On what is the lamp?            post   

  hallucinated_answer                                 hallucinated_trait  \
0               right  {'obj': {'id': '1082570', 'name': 'helmet'}, '...   
1             plastic  {'obj': {'id': '1082576', 'name': 'planter'}, ...   
2                left  {'obj': {'id': '1082566', 'name': 'lamp'}, 'at...   
3               fence  {'subject': {'id': '1082566', 'name': 'lamp'},...   
4            sidewalk  {'subject': {'id': '1082566', 'name': 'lamp'},...   

                                            metadata  
0  {'source': 'GQA', 'hallucinated_answer_source'...  
1  {'source': 'GQA', 'hallucinated_answer_source'...  
2  {'source': 'GQA', 'hallucinated_answer_source'...  
3  {'source': 'GQA', 'hallucinated_answer_source'...  
4  {'source': 'GQA', 'hallucinated_answer_source'...

In [22]:
df["question_id"].nunique()

159612

In [23]:
df.shape

(159612, 10)

In [24]:
df["semantic_type"].value_counts()

semantic_type
attribute       75627
object          40816
relationship    39085
scene            4084
Name: count, dtype: int64

In [25]:
df["semantic_type"].value_counts()

semantic_type
attribute       75627
object          40816
relationship    39085
scene            4084
Name: count, dtype: int64

In [26]:
vqa = pd.read_json("/Data2/Arun-UAV/NLP/vision_halu/haloc/train_dataset/halloc_vqa.json")
instruct = pd.read_json("/Data2/Arun-UAV/NLP/vision_halu/haloc/train_dataset/halloc_instruct.json")
caption = pd.read_json("/Data2/Arun-UAV/NLP/vision_halu/haloc/train_dataset/halloc_caption.json")

In [42]:
total_df = pd.concat([vqa, instruct, caption])

In [54]:
import os
len(os.listdir("/Data2/Arun-UAV/NLP/vision_halu/visual_genome/target_images"))

26222

In [ ]:
path = "/Data2/Arun-UAV/NLP/vision_halu/visual_genome/VG_100K/"
target_files = [path+str(i)+".jpg" for i in total_df["image_id"].unique().tolist()]

In [53]:
import os
import shutil

# Example: list of image paths
image_paths = target_files

# Target folder where all images will be copied
target_folder = "/Data2/Arun-UAV/NLP/vision_halu/visual_genome/target_images"

# Ensure target folder exists
os.makedirs(target_folder, exist_ok=True)

# Copy each file
for src_path in image_paths:
    if os.path.isfile(src_path):
        # Extract just the filename (keeps it unique if they already are)
        filename = os.path.basename(src_path)
        dest_path = os.path.join(target_folder, filename)
        shutil.copy2(src_path, dest_path)  # preserves metadata
        print(f"Copied: {src_path} -> {dest_path}")
    else:
        print(f"Skipped (not found): {src_path}")


Copied: /Data2/Arun-UAV/NLP/vision_halu/visual_genome/VG_100K/2411114.jpg -> /Data2/Arun-UAV/NLP/vision_halu/visual_genome/target_images/2411114.jpg
Copied: /Data2/Arun-UAV/NLP/vision_halu/visual_genome/VG_100K/2387711.jpg -> /Data2/Arun-UAV/NLP/vision_halu/visual_genome/target_images/2387711.jpg
Copied: /Data2/Arun-UAV/NLP/vision_halu/visual_genome/VG_100K/2408027.jpg -> /Data2/Arun-UAV/NLP/vision_halu/visual_genome/target_images/2408027.jpg
Copied: /Data2/Arun-UAV/NLP/vision_halu/visual_genome/VG_100K/2356114.jpg -> /Data2/Arun-UAV/NLP/vision_halu/visual_genome/target_images/2356114.jpg
Copied: /Data2/Arun-UAV/NLP/vision_halu/visual_genome/VG_100K/2403909.jpg -> /Data2/Arun-UAV/NLP/vision_halu/visual_genome/target_images/2403909.jpg
Copied: /Data2/Arun-UAV/NLP/vision_halu/visual_genome/VG_100K/2328448.jpg -> /Data2/Arun-UAV/NLP/vision_halu/visual_genome/target_images/2328448.jpg
Copied: /Data2/Arun-UAV/NLP/vision_halu/visual_genome/VG_100K/2331472.jpg -> /Data2/Arun-UAV/NLP/vision_ha

In [ ]:
import os
import shutil

# Example: list of image paths
image_paths = [
    "/path/to/folder1/image_001.jpg",
    "/path/to/folder2/image_045.png",
    "/path/to/folder3/photo_123.jpeg",
]

# Target folder where all images will be copied
target_folder = "/path/to/target_folder"

# Ensure target folder exists
os.makedirs(target_folder, exist_ok=True)

# Copy each file
for src_path in image_paths:
    if os.path.isfile(src_path):
        # Extract just the filename (keeps it unique if they already are)
        filename = os.path.basename(src_path)
        dest_path = os.path.join(target_folder, filename)
        shutil.copy2(src_path, dest_path)  # preserves metadata
        print(f"Copied: {src_path} -> {dest_path}")
    else:
        print(f"Skipped (not found): {src_path}")


(101442, 10)

In [35]:
all_datasets = [caption]
folder_path = "/Data2/Arun-UAV/NLP/vision_halu/haloc/train_dataset/caption/" 
for dataset in all_datasets:
    
    data_h = dataset[dataset["qa_ids"].apply(lambda x: len(x) != 0)]
    data_h_train = data_h[data_h["split"] == "train"]
    data_h_test = data_h[data_h["split"] == "test"]
    data_nh = dataset[dataset["qa_ids"].apply(lambda x: len(x) == 0)]
    data_nh_train = data_nh[data_nh["split"] == "train"]
    data_nh_test = data_nh[data_nh["split"] == "test"]
    
    data_h_train.to_csv(folder_path + "tp_train.csv")
    data_h_test.to_csv(folder_path + "tp_test.csv")
    data_nh_train.to_csv(folder_path + "tn_train.csv")
    data_nh_test.to_csv(folder_path + "tn_test.csv")
    

# intruction

In [37]:
data = pd.read_csv("/Data2/Arun-UAV/NLP/vision_halu/haloc/train_dataset/instruct/tp_train.csv")

In [39]:
data.head(3)

Unnamed: 0                                source_text  \
0           0               No, the bottle is on a sink.   
1           1        The jar is in the top of the image.   
2           2  The frisbee is on the right of the image.   

                        source_metadata qa_metadata         qa_ids  \
0  {'id': '001001100', 'source': 'GQA'}          {}  ['001001100']   
1  {'id': '001001148', 'source': 'GQA'}          {}  ['001001148']   
2  {'id': '001002646', 'source': 'GQA'}          {}  ['001002646']   

                                              prompt  image_id  \
0              <image>Do you see a bottle on a desk?   2324272   
1            <image>Locate the jar within the image.   2324272   
2  <image>Does the frisbee appear on the left sid...   2416944   

                          hallucinated_text  \
0             Yes, the bottle is on a desk.   
1    The jar is at the bottom of the image.   
2  The frisbee is to the left of the image.   

                                         annotations  split          id  
0  {'object': [{'obj': {'id': None, 'name': 'desk...  train  instruct_1  
1  {'object': [], 'attribute': [{'obj': {'id': '9...  train  instruct_2  
2  {'object': [], 'attribute': [{'obj': {'id': '3...  train  instruct_3